In [1]:
import pandas as pd
import numpy as np
import nltk
import pyspark
import matplotlib.pyplot as plt
import os.path as osp
import os
import shutil
from open_secrets_schema import Schema
import sys
from IPython.display import display, HTML

%matplotlib notebook

Load past-years campaign finance data - this data was downloaded on 10/21/2018 and so follows the most up-to-date schema as of time of creation. Schema strings are borrowed from the `pq_crp_*18` notebooks for this reason.

In [2]:
!whoami

matt


In [3]:
!pwd

/home/matt/etl


In [4]:
!ls

bill-metadata			 open-secrets-pastyears.ipynb
bill-text			 open_secrets_schema.py
bill-text.ipynb			 propublica-bill-meta.ipynb
legislators			 __pycache__
open-secrets			 unitedstates-legislators.ipynb
open-secrets-expenditures.ipynb  views
open-secrets.ipynb


In [5]:
os.chdir('open-secrets')

In [6]:
!ls

CampaignFin00.zip  CampaignFin08.zip  CampaignFin16.zip  CampaignFin94.zip
CampaignFin02.zip  CampaignFin10.zip  CampaignFin18	 CampaignFin96.zip
CampaignFin04.zip  CampaignFin12.zip  CampaignFin90.zip  CampaignFin98.zip
CampaignFin06.zip  CampaignFin14.zip  CampaignFin92.zip  Expend18


# `cands18`

`cands18` schema string: https://www.opensecrets.org/resources/datadictionary/Data%20Dictionary%20Candidates%20Data.htm

In [7]:
cands18SchemaStr = [
'''Cycle
Last year (even year) of the federal two year election cycle
Text (4)
FEC''',

'''FECCandID
Assigned by FEC and selected by CRP as the active, should multiples exist.
Text (9)
FEC''',

'''CID
Unique identifier for each candidate. Every candidate should have one and only one CID throughout all cycles. Recipid for candidates is based on CID.
Text (9)
CRP''',

'''FirstLastP
Candidate name in format of firstname lastname and party in parens, like Steve Kagen (D)
Text (50)
CRP''',

'''Party
The party of the candidate. "D" for Democratic, "R" for Republican", "I" for Independent, "L" for Libertarian", "3" for other third party and "U" for Unknown.
Text (1)
CRP''',

'''DistIDRunFor
Four character identifier of the office sought by the candidate. For congressional races, the first two characters are the state and the next two are the district for House candidates and "S1" or "S2" for Senate candidates. "PRES" indicates a presidential candidate.
Text (4)
CRP''',

'''DistIDCurr
Four character identifier of the office currently held (if any) by the candidate. For House members, the first two characters are the state and the next two are the district. For Senators the first two characters are the state and the last two characters are "S1" or "S2". "PRES" indicates a presidential candidate. For non-incumbents, this field is blank. If a member of Congress dies or leaves office, this field should become blank. This field is frozen on election day. For cycles prior to the current cycle, DistidCurr reflects office held on Election Day of the Cycle.
Text (4)
CRP''',

'''CurrCand
This field indicates whether the candidate is currently running for federal office - "Y" means yes, otherwise this field is blank. If a candidate loses a primary or drops out of the race, this field becomes blank. This field is frozen on Election Day, and thus for previous cycles can be used to show the candidate who ran in the general election.
Text (1)
CRP''',

'''CycleCand
This field indicates whether the candidate ever ran for federal office during the cycle in question. Like CurrCand, "Y" means yes and blank means no. This field should be "Y" for any candidate who filed to run for office or otherwise formally declared intention to run. This does NOT change if the candidate drops out or loses a primary. Be aware that we've tightened the definition in recent cycles - for older data, CycleCand is likely to cast a broader net. Also note that incumbents are usually assumed to be running for re-election and get a "Y" in CycleCand unless there is evidence to the contrary.
Text (1)
CRP''',

'''CRPICO
Identifies type of candidate - "I" is incumbent, "C" is challenger, "O" is open seat. This may be blank if the candidate is neither a member of Congress nor running this cycle. Note this is based on the office sought. A House incumbent running for the Senate would have a CRPICO of "C" or "O", not "I."
Text (1)
CRP''',

'''RecipCode
A two-character code defining the type of candidate. The first character is party ("D" for Democratic, "R" for Republican, "3" for Independent or third party, "U" for Unknown.) The second character is "W" for Winner, "L" for Loser, "I" for incumbent, "C" for Challenger, "O" for "Open Seat", and "N" for Non-incumbent. Incumbent, Challenger and Open Seat are based on CRPICO. "N" is reserved for candidates that are neither in office nor running during the cycle in question. This lives in dbo_CandsCRP.
Text (2)
CRP''',

'''NoPacs
Indicates whether candidate has publicly committed to forego contributions from PACs
Text (1)
CRP'''
]

# `cmtes18`

`cmtes18` schema string: https://www.opensecrets.org/resources/datadictionary/Data%20Dictionary%20Candidates%20Data.htm

In [8]:
cmtes18SchemaStr = [
'''Cycle
Last year (even year) of the federal 2-year election cycle
Text (4)
FEC''',

'''CmteID
Unique ID given by FEC to each committee.
Text (9)
FEC''',

'''PACShort
Standardized committee name based on PAC's sponsor.
Text (50)
CRP''',

'''Affiliate
Usually blank. For leadpacs, shows the sponsoring member.
Text (50)
CRP''',

'''Ultorg
The standardized parent organization for the organization listed in the PACShort field. If there is no parent identified, this field will be equal to PACShort.
Text (50)
CRP''',

'''RecipID
For candidate committees this will be the candidate's CID. Otherwise, it will be the same as CmteID.
Text (9)
CRP''',

'''RecipCode
A two-character code defining the type of recipient. For candidates, the first character is party ("D" for Democratic, "R" for Republican, "3" for Independent, Libertarian or third party, "U" for Unknown.) The second character is "W" for Winner, "L" for Loser, "I" for incumbent, "C" for Challenger, "O" for "Open Seat", and "N" for Non-incumbent. "N" is reserved for candidates that are neither in office nor running during the cycle in question. For party committees, the first character is party and the second character is "P." For PACs, the first character is "P" and for outside spending groups, "O". For both, the second character is "B" for Business, "L" for Labor", "I" for Ideological, "O" for "Other" and "U" for unknown.
Text (2)
CRP''',

'''FECCandID
Unique ID given to candidates by FEC.
Text (9)
FEC''',

'''Party
(D,R,3,I,L) Will be null or empty if committee is not a party, joint fundraising, leadership or candidate committee.
Text (1)
CRP/FEC''',

'''PrimCode
The standard five character code identifying the committee's industry or ideology.
Text (5)
CRP''',

'''Source
Indicates how the PrimCode was determined.
Text (5)
CRP''',

'''Sensitive
If "Y", the committee has significant business in multiple industries, some of which fall under the jurisdiction of specific congressional committees.
Text (1)
CRP''',

'''Foreign
This is a bit field. Off/False indicate that the company is not owned by a foreign entity. Those that are owned by a foreign entity are on/True, sometimes "-1".
Bit
CRP''',

'''Active
Determines if cmte is active in the cycle - 0 is no and 1 is yes
Integer
CRP'''
]

# `indivs18`

`indivs18` schema string: https://www.opensecrets.org/resources/datadictionary/Data%20Dictionary%20for%20Individual%20Contribution%20Data.htm

In [9]:
indivs18SchemaStr = [
'''Cycle
Last year (even year) of the federal 2-year election cycle
Text (4)
FEC''',

'''FECTransID
A unique record identifier within a given cycle.
Text (19)
FEC''',

'''ContribID
A unique identifier for individual donors.  Family groups match on first 11 chars
Text (12)
CRP''',

'''Contrib
The name of the contributor, usually in the format Last name, First Name.
Text (50)
FEC''',

'''RecipID
The recipient's id number. If the contribution is to a candidate this will be the candidate's unique candidate id number. Otherwise, it will be the FEC committee id number.
Text (9)
CRP''',

'''Orgname
The standardized organization name for the contributor. This is usually based on the donor's employer. The donor may not have an income producing occupation (e.g. homemaker)
Text (50)
CRP''',

'''UltOrg
The standardized parent organization for the organization listed in the Orgname field. If there is no parent identified, this field will be blank or null.
Text (50)
CRP''',

'''RealCode
The standard five character code identifying the donor's industry or ideology. Usually based on Orgname (e.g., the orgname "Microsoft Corp" would normally get realcode C5120 for computer software.)
Text (5)
CRP''',

'''Date
The reported date of the contribution.
MM/DD/YYYY
FEC''',

'''Amount
The amount contributed. This will be negative for refunds.
Integer
FEC''',

'''Street
2000+ cycle only, and only for committees that file electronically
Text (40)
FEC''',

'''City
The donor's city. This could be based on a home address or an employer's address. 
Text (30)
FEC''',

'''State
The donor's state. This could be based on a home address or an employer's address.
Text (2)
FEC''',

'''Zip
The donor's zip code. This could be based on a home address or an employer's address.
Text (5)
FEC''',

'''RecipCode
A two-character code defining the type of recipient. For candidates, the first character is party ("D" for Democratic, "R" for Republican, "3" for Independent, Libertarian or third party, "U" for Unknown.) The second character is "W" for Winner, "L" for Loser, "I" for incumbent, "C" for Challenger, "O" for "Open Seat", and "N" for Non-incumbent. "N" is reserved for candidates that are neither in office nor running during the cycle in question. For party committees, the first character is party and the second character is "P." For PACs, the first character is "P" and the second character is "B" for Business, "L" for Labor", "I" for Ideological, "O" for "Other" and "U" for unknown.
Text (2)
CRP''',

'''Type
The transaction type code for the contribution. 15 is a contribution, 15e is an earmarked contribution (made through a group such as Club for Growth or Emily's List), 15j is a contribution through a joint fund raising committee and 22y is a refund. "10" indicates "soft" or nonfederal money for the 2002 cycle and earlier. For the 2004 cycle and later type "10" indicates Levin funds.or outside spending.
Text (3)
FEC''',

'''CmteID
The committee id number for the recipient. Note that a candidate can have more than one committee — this field indicates the exact committee receiving the contribution.
Text (9)
FEC''',

'''OtherID
The committee id number for the intermediary party to earmarked contributions.
Text (9)
FEC''',

'''Gender
The donor's gender. Can also be "U" if unknown or "N" if the name is ambiguous.
Text (1)
CRP''',

'''Microfilm
Refers to specific page of FEC report images on which this transaction appears.
Text (11)
FEC''',

'''Occupation
The donor's disclosed occupation.
Text (38)
FEC''',

'''Employer
The donor's s disclosed employer
Text (38)
FEC''',

'''Source
Indicates how the RealCode was determined — see the How to Use Source in the OpenSecrets OpenData Guide
Text (5)
<NOT SPECIFIED>'''
]

# `pac_other18`

`pac_other18` schema string: https://www.opensecrets.org/resources/datadictionary/Data%20Dictionary%20PAC%20to%20PAC%20Data.htm

In [10]:
pac_other18SchemaStr = ['''Cycle
Last year (even year) of the federal 2-year election cycle
Text (4)
FEC''',

'''FECRecNo
A unique record identifier within a given cycle.
Text (19)
FEC''',

'''Filerid
The committee id number for the PAC making the filing. Refers to donor if Type 2* or recipient if Type=1*.
Text (9)
FEC''',

'''DonorCmte
The standardized name for the donor based on the name of the PAC's sponsor.
Text (50)
CRP''',

'''ContribLendTrans
Reported name of the donor if Type=1* or the recipient if Type=2*.
Text (50)
FEC''',

'''City
The donor's city. This could be based on a home address or an employer's address.
Text (30)
FEC''',

'''State
The donor's state. This could be based on a home address or an employer's address.
Text (2)
FEC''',

'''Zip
The donor's zip code. This could be based on a home address or an employer's address.
Text (5)
FEC''',

'''FECOccEmp
The donor's disclosed employer and/or occupation.
Text (38)
FEC''',

'''Primcode
The primary industry/ideological code for the donor PAC's sponsor.
Text (5)
CRP''',

'''Date
The reported date of the contribution.
Date
FEC''',

'''Amount
The amount contributed. This will be negative for refunds.
Float
FEC''',

'''RecipID
The recipient's id number. If the contribution is to a candidate this will be the candidate's unique candidate id number. Otherwise, it will be the FEC committee id number.
Text (9)
CRP''',

'''Party
The party (if any) of the recipient. "D" for Democratic, "R" for Republican", "I" for Independent, "L" for Libertarian", "3" for other third party and "U" for Unknown. This field will be blank or null for PACs other than leadership PACs.
Text (1)
CRP''',

'''Otherid
Committee id for donor if Type=1* or recipient if Type=2*.
Text (9)
FEC''',

'''RecipCode
A two character code defining the type of recipient. For candidates, the first character is party ("D" for Democratic, "R" for Republican, "3" for Independent, Libertarian or third party, "U" for Unknown.) The second character is "W" for Winner, "L" for Loser, "I" for incumbent, "C" for Challenger, "O" for "Open Seat", and "N" for Non-incumbent. "N" is reserved for candidates that are neither in office nor running during the cycle in question. For party committees, the first character is party and the second character is "P." For PACs, the first character is "P" and for outside spending groups, the first character is "O". For both, the second character is "B" for Business, "L" for Labor", "I" for Ideological, "O" for "Other" and "U" for unknown.
Text (2)
CRP''',

'''RecipPrimcode
The industry/ideological code for the recipient - codes beginning with Z1 are candidate committees, codes beginning with Z5 are party committees and codes beginning with J2 are leadership PACs.
Text (5)
CRP''',

'''Amend
Whether the record comes from an amended report
Text (1)
FEC''',

'''Report
The type of report - 1st quarter, year end, etc.
Text (3)
FEC''',

'''PG
Whether the contribution is for a Primary ("P") or General ("G") election.
Text (1)
FEC''',

'''Microfilm
The FEC microfilm record for the contribution
Text (11)
FEC''',

'''Type
The transaction type code for the contribution. 11 is a tribal contribution, 22Z is a contribution refund to a candidate or committee, 24G is a Transfer to an affiliated committee, 24K is a direct contribution, 24R is a election recount disbursement and 24Z is an in kind contribution
Text (3)
FEC''',

'''RealCode
The standard five character code identifying the donor's industry or ideology.Usually based on Primcode. Sometimes a PAC sponsor will have secondary interests which may replace the main realcode depending on recipient. For example, Boeing is primarily Air Transport but has Air Defense interests. Thus Boeing contributions to members of the Armed Services committee would have a realcode of Air Defense.
Text (5)
CRP''',

'''Source
Indicates how the Realcode was determined.
Text (5)
CRP'''
]

# `pacs18`

`pacs18` schema string: https://www.opensecrets.org/resources/datadictionary/Data%20Dictionary%20for%20PAC%20to%20Cands%20Data.htm

In [11]:
pacs18SchemaStr = [
'''Cycle
Last year (even year) of the federal 2-year election cycle
Text (4)
FEC''',

'''FECRecNo
A unique record identifier within a given cycle.
Text (19)
FEC''',

'''PACID
The committee id number for the PAC making the contribution.
Text (9)
FEC''',

'''CID
A unique identifier for candidates that is constant throughout cycles.
Text (9)
CRP''',

'''Amount
The amount contributed. This will be negative for refunds.
float
FEC''',

'''Date
The reported date of the contribution.
Date
FEC''',

'''RealCode
The standard five character code identifying the donor's industry or ideology. Usually based on Primcode. Sometimes a PAC sponsor will have secondary interests which may replace the main realcode depending on recipient. For example, Boeing is primarily Air Transport but has Air Defense interests. Thus Boeing contributions to members of the Armed Services committee would have a realcode of Air Defense.
Text (5)
CRP''',

'''Type
The transaction type code for the contribution. 24A is an Independent Expenditure against the candidate, 24C is a coordinated expenditure, 24E is an independent expenditure for the candidate, 24F is a communication cost for the candidate, 24K is a direct contribution, 24N is a communication cost against the candidate and 24Z is an in kind contribution
Text (3)
FEC''',

'''DI
Whether the contribution is direct ("D") or indirect ("I."). Indirect contributions include independent expenditures and communications costs, are not subject to contribution limits and must be made completely independently of the candidate. Indirect contributions can also be against the candidate.
Text (1)
CRP''',

'''FECCandID
FECCandID of recipient candidate
Text (9)
FEC'''
]

# Extract files from zips

In [12]:
for i in filter(lambda x: x.lower().endswith('.zip'), os.listdir()):
    cmd = f'unzip -q {i} -d {i[:-4]}'
    display(HTML(f'<h2>{i}</h2>'))
    print(cmd)
    !$cmd
    display(HTML('<hr>'))

unzip -q CampaignFin04.zip -d CampaignFin04


unzip -q CampaignFin00.zip -d CampaignFin00


unzip -q CampaignFin92.zip -d CampaignFin92


unzip -q CampaignFin08.zip -d CampaignFin08


unzip -q CampaignFin02.zip -d CampaignFin02


...

unzip -q CampaignFin10.zip -d CampaignFin10


unzip -q CampaignFin14.zip -d CampaignFin14


unzip -q CampaignFin98.zip -d CampaignFin98


unzip -q CampaignFin96.zip -d CampaignFin96


unzip -q CampaignFin16.zip -d CampaignFin16


In [19]:
def etl_text_file(text_file_path, schema_str, table_name, data_source_name, column_datetime_formats=None,
                  csv_quotechar='|', csv_delimiter=','):
    schema = Schema(schema_str)
    schema.register_column_datetime_formats(column_datetime_formats)
    textFileName = osp.split(text_file_path)[1]
    stagingFolder = f'/staging/{table_name}'
    !hdfs dfs -rm -r -f {stagingFolder}/{textFileName}
    !hdfs dfs -mkdir -p {stagingFolder}
    !hdfs dfs -put {text_file_path} {stagingFolder}/{textFileName}
    !hdfs dfs -chmod -R 777 {stagingFolder}
    with open(f'{table_name}.sql', 'w') as f:
        f.write(schema.hive_ddl(tableName=table_name, externalTableLocation=stagingFolder,
                                csv_quotechar=csv_quotechar, csv_delimiter=csv_delimiter))
    !/opt/anaconda3/bin/beeline -u jdbc:hive2://cap1:10000 -n matt -p anything -f {table_name}.sql
    
    # Convert to the proper schema and write as parquet
    finalTableName = f'pq_{data_source_name}_{table_name}'
    with open(f'{finalTableName}.sql', 'w') as f:
        f.write(schema.hive_ddl_parquet_alter(tableName=finalTableName, originalTableName=table_name))
    
    dfWithSchema = sc.sql(schema.hive_ddl_parquet_select(tableName=finalTableName, originalTableName=table_name))
    sc.sql(f'DROP TABLE IF EXISTS {finalTableName}')
    dfWithSchema.write.saveAsTable(finalTableName)
    !/opt/anaconda3/bin/beeline -u jdbc:hive2://cap1:10000 -n matt -p anything -f {finalTableName}.sql
    
    # clean up -- drop the intermediate (text file) table and delete staged data from HDFS
    sc.sql(f'DROP TABLE {table_name}')
    !hdfs dfs -rm -r -f {stagingFolder}
    
    print('done')

In [32]:
def etl_text_file_beeline(text_file_path, schema_str, table_name,
                          data_source_name, column_datetime_formats=None,
                          csv_quotechar='|', csv_delimiter=','):
    schema = Schema(schema_str)
    schema.register_column_datetime_formats(column_datetime_formats)
    textFileName = osp.split(text_file_path)[1]
    stagingFolder = f'/staging/{table_name}'
    !hdfs dfs -rm -r -f {stagingFolder}/{textFileName}
    !hdfs dfs -mkdir -p {stagingFolder}
    !hdfs dfs -put {text_file_path} {stagingFolder}/{textFileName}
    !hdfs dfs -chmod -R 777 {stagingFolder}
    with open(f'{table_name}.sql', 'w') as f:
        f.write(schema.hive_ddl(tableName=table_name, externalTableLocation=stagingFolder,
                                csv_quotechar=csv_quotechar, csv_delimiter=csv_delimiter))
    !/opt/anaconda3/bin/beeline -u jdbc:hive2://cap1:10000 -n matt -p anything -f {table_name}.sql
    
    # Convert to the proper schema and write as parquet
    finalTableName = f'pq_{data_source_name}_{table_name}'
    with open(f'{finalTableName}.sql', 'w') as f:
        f.write(schema.hive_ddl_parquet(tableName=finalTableName, originalTableName=table_name))

    
    # write table with spark-sql because beeline has a bug
    # ... or more specifically, a bee...
    !/opt/anaconda3/bin/spark-sql -f {finalTableName}.sql
    
    # clean up -- drop the intermediate (text file) table and delete staged data from HDFS

    dropTable = f'DROP TABLE {table_name};'
    !/opt/anaconda3/bin/beeline -u jdbc:hive2://cap1:10000 -n matt -p anything -e '{dropTable}'
    !hdfs dfs -rm -r -f {stagingFolder}
    
    print('done')

In [22]:
dt_by_dataset = {
    'cands': None,
    'cmtes': None,
    'pac_other': {'Date': 'MM/dd/yyyy'},
    'indivs': {'Date': 'MM/dd/yyyy'},
    'pacs': {'Date': 'MM/dd/yyyy'}
}

In [36]:
TESTING = False

# 1990 and 1992 already loaded and validated during testing,
#  so start with year=1994.
for yr in map(lambda x: str(x)[-2:], range(94, 118, 2)):
    os.chdir('/home/matt/etl/open-secrets')
    dirName = f'CampaignFin{yr}'
    display(HTML(f'<h2>{dirName}</h2>'))
    os.chdir(dirName)
    for dsName, schemaStr in zip(['cands', 'cmtes', 'pac_other',
                                  'indivs', 'pacs'],
                                 [cands18SchemaStr,
                                  cmtes18SchemaStr,
                                  pac_other18SchemaStr,
                                  indivs18SchemaStr,
                                  pacs18SchemaStr]):
        dsFileName = f'{dsName}{yr}.txt'
        display(HTML(f'<h4>{dsFileName}</h4>'))
        etl_text_file_beeline(dsFileName,
                              schemaStr,
                              f'{dsName}{yr}',
                              data_source_name='crp',
                              column_datetime_formats=dt_by_dataset[dsName])
        if TESTING:
            break
    if TESTING:
        break

2018-10-21 20:01:43,241 WARN util.NativeCodeLoader: Unable to load native-hadoop library for your platform... using builtin-java classes where applicable
2018-10-21 20:01:45,295 WARN util.NativeCodeLoader: Unable to load native-hadoop library for your platform... using builtin-java classes where applicable
2018-10-21 20:01:47,346 WARN util.NativeCodeLoader: Unable to load native-hadoop library for your platform... using builtin-java classes where applicable
2018-10-21 20:01:49,696 WARN util.NativeCodeLoader: Unable to load native-hadoop library for your platform... using builtin-java classes where applicable
Connecting to jdbc:hive2://cap1:10000
2018-10-21 20:01:51 INFO  Utils:310 - Supplied authorities: cap1:10000
2018-10-21 20:01:51 INFO  Utils:397 - Resolved authority: cap1:10000
2018-10-21 20:01:51 INFO  HiveConnection:203 - Will try to open client transport with JDBC Uri: jdbc:hive2://cap1:10000
Connected to: Spark SQL (version 2.3.2)
Driver: Hive JDBC (version 1.2.1.spark2)
Trans

2018-10-21 20:01:58 INFO  ContextHandler:781 - Started o.s.j.s.ServletContextHandler@134f8ef6{/static,null,AVAILABLE,@Spark}
2018-10-21 20:01:58 INFO  ContextHandler:781 - Started o.s.j.s.ServletContextHandler@3d88e6b9{/,null,AVAILABLE,@Spark}
2018-10-21 20:01:58 INFO  ContextHandler:781 - Started o.s.j.s.ServletContextHandler@22bf9122{/api,null,AVAILABLE,@Spark}
2018-10-21 20:01:58 INFO  ContextHandler:781 - Started o.s.j.s.ServletContextHandler@5700c9db{/jobs/job/kill,null,AVAILABLE,@Spark}
2018-10-21 20:01:58 INFO  ContextHandler:781 - Started o.s.j.s.ServletContextHandler@671d03bb{/stages/stage/kill,null,AVAILABLE,@Spark}
2018-10-21 20:01:58 INFO  SparkUI:54 - Bound SparkUI to 0.0.0.0, and started at http://cap1:4042
2018-10-21 20:01:58 INFO  Executor:54 - Starting executor ID driver on host localhost
2018-10-21 20:01:58 INFO  Utils:54 - Successfully started service 'org.apache.spark.network.netty.NettyBlockTransferService' on port 40279.
2018-10-21 20:01:58 INFO  NettyBlockTransfe

2018-10-21 20:02:02 INFO  HiveMetaStore:746 - 0: get_database: default
2018-10-21 20:02:02 INFO  audit:371 - ugi=matt	ip=unknown-ip-addr	cmd=get_database: default	
2018-10-21 20:02:02 INFO  HiveMetaStore:746 - 0: get_table : db=default tbl=pq_crp_cands94
2018-10-21 20:02:02 INFO  audit:371 - ugi=matt	ip=unknown-ip-addr	cmd=get_table : db=default tbl=pq_crp_cands94	
2018-10-21 20:02:02 INFO  HiveMetaStore:746 - 0: get_table : db=default tbl=pq_crp_cands94
2018-10-21 20:02:02 INFO  audit:371 - ugi=matt	ip=unknown-ip-addr	cmd=get_table : db=default tbl=pq_crp_cands94	
2018-10-21 20:02:02 INFO  FileUtils:501 - Creating directory if it doesn't exist: hdfs://cap1/user/hive/warehouse/pq_crp_cands94/.hive-staging_hive_2018-10-21_20-02-02_078_5876553231771865072-1
2018-10-21 20:02:02 INFO  FileOutputCommitter:108 - File Output Committer Algorithm version is 1
2018-10-21 20:02:02 INFO  SQLHadoopMapReduceCommitProtocol:54 - Using output committer class org.apache.hadoop.mapreduce.lib.output.FileO

2018-10-21 20:02:04 INFO  log:217 - Updating table stats fast for pq_crp_cands94
2018-10-21 20:02:04 INFO  log:219 - Updated size of table pq_crp_cands94 to 155380
2018-10-21 20:02:04 INFO  HiveMetaStore:746 - 0: get_database: default
2018-10-21 20:02:04 INFO  audit:371 - ugi=matt	ip=unknown-ip-addr	cmd=get_database: default	
2018-10-21 20:02:04 INFO  HiveMetaStore:746 - 0: get_table : db=default tbl=pq_crp_cands94
2018-10-21 20:02:04 INFO  audit:371 - ugi=matt	ip=unknown-ip-addr	cmd=get_table : db=default tbl=pq_crp_cands94	
2018-10-21 20:02:04 INFO  HiveMetaStore:746 - 0: get_table : db=default tbl=pq_crp_cands94
2018-10-21 20:02:04 INFO  audit:371 - ugi=matt	ip=unknown-ip-addr	cmd=get_table : db=default tbl=pq_crp_cands94	
Time taken: 3.571 seconds
2018-10-21 20:02:04 INFO  SparkSQLCLIDriver:951 - Time taken: 3.571 seconds
2018-10-21 20:02:04 INFO  HiveMetaStore:746 - 0: get_database: default
2018-10-21 20:02:04 INFO  audit:371 - ugi=matt	ip=unknown-ip-addr	cmd=get_database: default

2018-10-21 20:02:05 INFO  HiveMetaStore:746 - 0: get_table : db=default tbl=pq_crp_cands94
2018-10-21 20:02:05 INFO  audit:371 - ugi=matt	ip=unknown-ip-addr	cmd=get_table : db=default tbl=pq_crp_cands94	
2018-10-21 20:02:05 INFO  HiveMetaStore:746 - 0: get_table : db=default tbl=pq_crp_cands94
2018-10-21 20:02:05 INFO  audit:371 - ugi=matt	ip=unknown-ip-addr	cmd=get_table : db=default tbl=pq_crp_cands94	
2018-10-21 20:02:05 INFO  HiveMetaStore:746 - 0: get_table : db=default tbl=pq_crp_cands94
2018-10-21 20:02:05 INFO  audit:371 - ugi=matt	ip=unknown-ip-addr	cmd=get_table : db=default tbl=pq_crp_cands94	
2018-10-21 20:02:05 INFO  HiveMetaStore:746 - 0: get_table : db=default tbl=pq_crp_cands94
2018-10-21 20:02:05 INFO  audit:371 - ugi=matt	ip=unknown-ip-addr	cmd=get_table : db=default tbl=pq_crp_cands94	
2018-10-21 20:02:05 INFO  HiveMetaStore:746 - 0: alter_table: db=default tbl=pq_crp_cands94 newtbl=pq_crp_cands94
2018-10-21 20:02:05 INFO  audit:371 - ugi=matt	ip=unknown-ip-addr	cmd=

...

2018-10-21 20:42:35 INFO  Executor:54 - Starting executor ID driver on host localhost
2018-10-21 20:42:35 INFO  Utils:54 - Successfully started service 'org.apache.spark.network.netty.NettyBlockTransferService' on port 44425.
2018-10-21 20:42:35 INFO  NettyBlockTransferService:54 - Server created on cap1:44425
2018-10-21 20:42:35 INFO  BlockManager:54 - Using org.apache.spark.storage.RandomBlockReplicationPolicy for block replication policy
2018-10-21 20:42:35 INFO  BlockManagerMaster:54 - Registering BlockManager BlockManagerId(driver, cap1, 44425, None)
2018-10-21 20:42:35 INFO  BlockManagerMasterEndpoint:54 - Registering block manager cap1:44425 with 366.3 MB RAM, BlockManagerId(driver, cap1, 44425, None)
2018-10-21 20:42:35 INFO  BlockManagerMaster:54 - Registered BlockManager BlockManagerId(driver, cap1, 44425, None)
2018-10-21 20:42:35 INFO  BlockManager:54 - Initialized BlockManager: BlockManagerId(driver, cap1, 44425, None)
2018-10-21 20:42:35 INFO  ContextHandler:781 - Started

2018-10-21 20:42:39 INFO  FileUtils:501 - Creating directory if it doesn't exist: hdfs://cap1/user/hive/warehouse/pq_crp_pacs16
2018-10-21 20:42:39 INFO  HiveMetaStore:746 - 0: get_database: default
2018-10-21 20:42:39 INFO  audit:371 - ugi=matt	ip=unknown-ip-addr	cmd=get_database: default	
2018-10-21 20:42:39 INFO  HiveMetaStore:746 - 0: get_table : db=default tbl=pq_crp_pacs16
2018-10-21 20:42:39 INFO  audit:371 - ugi=matt	ip=unknown-ip-addr	cmd=get_table : db=default tbl=pq_crp_pacs16	
2018-10-21 20:42:39 INFO  HiveMetaStore:746 - 0: get_table : db=default tbl=pq_crp_pacs16
2018-10-21 20:42:39 INFO  audit:371 - ugi=matt	ip=unknown-ip-addr	cmd=get_table : db=default tbl=pq_crp_pacs16	
2018-10-21 20:42:39 INFO  FileUtils:501 - Creating directory if it doesn't exist: hdfs://cap1/user/hive/warehouse/pq_crp_pacs16/.hive-staging_hive_2018-10-21_20-42-39_302_8207540442381039962-1
2018-10-21 20:42:39 INFO  FileOutputCommitter:108 - File Output Committer Algorithm version is 1
2018-10-21 20:

2018-10-21 20:42:50 INFO  HiveMetaStore:746 - 0: get_table : db=default tbl=pq_crp_pacs16
2018-10-21 20:42:50 INFO  audit:371 - ugi=matt	ip=unknown-ip-addr	cmd=get_table : db=default tbl=pq_crp_pacs16	
2018-10-21 20:42:50 INFO  HiveMetaStore:746 - 0: get_database: default
2018-10-21 20:42:50 INFO  audit:371 - ugi=matt	ip=unknown-ip-addr	cmd=get_database: default	
2018-10-21 20:42:50 INFO  HiveMetaStore:746 - 0: get_table : db=default tbl=pq_crp_pacs16
2018-10-21 20:42:50 INFO  audit:371 - ugi=matt	ip=unknown-ip-addr	cmd=get_table : db=default tbl=pq_crp_pacs16	
2018-10-21 20:42:50 INFO  HiveMetaStore:746 - 0: get_table : db=default tbl=pq_crp_pacs16
2018-10-21 20:42:50 INFO  audit:371 - ugi=matt	ip=unknown-ip-addr	cmd=get_table : db=default tbl=pq_crp_pacs16	
2018-10-21 20:42:50 INFO  HiveMetaStore:746 - 0: get_table : db=default tbl=pq_crp_pacs16
2018-10-21 20:42:50 INFO  audit:371 - ugi=matt	ip=unknown-ip-addr	cmd=get_table : db=default tbl=pq_crp_pacs16	
2018-10-21 20:42:50 INFO  Hi

2018-10-21 20:42:50 INFO  log:217 - Updating table stats fast for pq_crp_pacs16
2018-10-21 20:42:50 INFO  log:219 - Updated size of table pq_crp_pacs16 to 8275836
Time taken: 0.148 seconds
2018-10-21 20:42:50 INFO  SparkSQLCLIDriver:951 - Time taken: 0.148 seconds
2018-10-21 20:42:50 INFO  HiveMetaStore:746 - 0: get_database: default
2018-10-21 20:42:50 INFO  audit:371 - ugi=matt	ip=unknown-ip-addr	cmd=get_database: default	
2018-10-21 20:42:50 INFO  HiveMetaStore:746 - 0: get_table : db=default tbl=pq_crp_pacs16
2018-10-21 20:42:50 INFO  audit:371 - ugi=matt	ip=unknown-ip-addr	cmd=get_table : db=default tbl=pq_crp_pacs16	
2018-10-21 20:42:50 INFO  HiveMetaStore:746 - 0: get_table : db=default tbl=pq_crp_pacs16
2018-10-21 20:42:50 INFO  audit:371 - ugi=matt	ip=unknown-ip-addr	cmd=get_table : db=default tbl=pq_crp_pacs16	
2018-10-21 20:42:50 INFO  HiveMetaStore:746 - 0: get_database: default
2018-10-21 20:42:50 INFO  audit:371 - ugi=matt	ip=unknown-ip-addr	cmd=get_database: default	
201

2018-10-21 20:42:51 INFO  HiveMetaStore:746 - 0: get_table : db=default tbl=pq_crp_pacs16
2018-10-21 20:42:51 INFO  audit:371 - ugi=matt	ip=unknown-ip-addr	cmd=get_table : db=default tbl=pq_crp_pacs16	
2018-10-21 20:42:51 INFO  HiveMetaStore:746 - 0: get_table : db=default tbl=pq_crp_pacs16
2018-10-21 20:42:51 INFO  audit:371 - ugi=matt	ip=unknown-ip-addr	cmd=get_table : db=default tbl=pq_crp_pacs16	
2018-10-21 20:42:51 INFO  HiveMetaStore:746 - 0: alter_table: db=default tbl=pq_crp_pacs16 newtbl=pq_crp_pacs16
2018-10-21 20:42:51 INFO  audit:371 - ugi=matt	ip=unknown-ip-addr	cmd=alter_table: db=default tbl=pq_crp_pacs16 newtbl=pq_crp_pacs16	
2018-10-21 20:42:51 INFO  log:217 - Updating table stats fast for pq_crp_pacs16
2018-10-21 20:42:51 INFO  log:219 - Updated size of table pq_crp_pacs16 to 8275836
Time taken: 0.136 seconds
2018-10-21 20:42:51 INFO  SparkSQLCLIDriver:951 - Time taken: 0.136 seconds
2018-10-21 20:42:51 INFO  HiveMetaStore:746 - 0: get_database: default
2018-10-21 20: